## Elevation rasters from the National National Map (USGS)

The [3D Elevation Program (3DEP)](https://www.usgs.gov/core-science-systems/ngp/3dep/about-3dep-products-services) is the source of the elevation products used by the National Map, which is maintained by the USGS. This is a nation-wide elevation data set provided as a web service through the [ArcGIS REST API Image Server](https://elevation.nationalmap.gov/arcgis/rest/services/3DEPElevation/ImageServer) with a 1m spatial resolution.

This API allows the user to perform many differnt server-side computations for topographic analysis such as aspect, slope, histograms of the entire image, etc. 

I chose to use the exportImage service to access and download a DEM (.tiff) of the Lower Brazos River in Texas.

In [1]:
import xarray as xr
import hvplot.xarray
import datashader
import cartopy.crs as ccrs
import geoviews as gv
import cmocean.cm as cmo

## Using the REST API

For this API, I created a query URL specifying the area of interest (AOI), coordinate reference system (CRS) for the AOI, size of the image in pixels, and CRS for the image. You can specify many more parameters, but I chose to leave them blank. 

I started with a coarse spatial resolution (100m) to troubleshoot my code, but when I used a finer resolution, the API failed without any feedback. This is strange because the API specifies a max spatial resolution of 1m and a max imagesize of 8000x8000. The API fails at a spatial resolution of 60m with an image size of 2736x4447 px, so I went with the largest file I could download at 70m resolution, 2345x3812 px, 35.76MB. 

### REST API Parameters

In [25]:
bbox = [789113, 4127884, 953283, 4394745] # [xmin, ymin, xmax, ymax]
crs = 32140
res = 75     # width of a pixel in meters
funcs = ["",                                # raw elevation values
         "{'rasterFunction':'Grayscale'}",  # relative elevation values
         "{'rasterFunction':'Aspect'}",     # Direction of faces
         "{'rasterFunction':'Slope'}"]      # Slope 

## Calcualte image size and build url

In [17]:
def build_url(res, bbox, crs, func):
    
    x_px = int((bbox[2] - bbox[0]) / res)   # calc image size based on desired resolution
    y_px = int((bbox[3] - bbox[1]) / res)
    
    server = 'https://elevation.nationalmap.gov/arcgis/rest/services/3DEPElevation/ImageServer/'
    query = 'exportImage?bbox={xmin}%2C{ymin}%2C{xmax}%2C{ymax}&bboxSR={crs}&size={x_px}%2C{y_px}&imageSR={crs}&time=&format=tiff&pixelType=F32&noData=&noDataInterpretation=esriNoDataMatchAny&interpolation=+RSP_BilinearInterpolation&compression=&compressionQuality=&bandIds=&mosaicRule=&renderingRule={func}&f=image' \
    .format(xmin=bbox[0], ymin=bbox[1], xmax=bbox[2], ymax=bbox[3], crs=crs, x_px=x_px, y_px=y_px, func=func)
    
    url = server + query

    return(url, (x_px, y_px))

In [26]:
tiff_url = build_url(res, bbox, crs, funcs[0])
print(tiff_url[0])  # url for image - click this link to download the image
print(tiff_url[1])  # dimensions for image

https://elevation.nationalmap.gov/arcgis/rest/services/3DEPElevation/ImageServer/exportImage?bbox=789113%2C4127884%2C953283%2C4394745&bboxSR=32140&size=2188%2C3558&imageSR=32140&time=&format=tiff&pixelType=F32&noData=&noDataInterpretation=esriNoDataMatchAny&interpolation=+RSP_BilinearInterpolation&compression=&compressionQuality=&bandIds=&mosaicRule=&renderingRule={'rasterFunction':'Grayscale'}&f=image
(2188, 3558)


In [9]:
from dask.distributed import Client

client = Client("tcp://127.0.0.1:51539")
client

<Client: 'tcp://127.0.0.1:51539' processes=4 threads=4, memory=8.59 GB>

In [22]:
%%time
dem = xr.open_rasterio(tiff_url[0])

CPU times: user 8.58 ms, sys: 11.7 ms, total: 20.3 ms
Wall time: 8.99 s


In [19]:
# this takes my computer a while to load 
%%time
dem.hvplot.image(width = 600,
                 height = 600,
                 crs = ccrs.epsg(crs),
                 rasterize=True)

CPU times: user 38.7 ms, sys: 30.4 ms, total: 69.2 ms
Wall time: 250 ms


:DynamicMap   [band]
   :Image   [x,y]   (value)